In [1]:
import definitions as df
import data_manipulation as dm
import sql_def as sql
import os
import numpy as np
import matplotlib.pyplot as plt
import plots
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
import math
import torch.nn.functional as F

Grabing the data from SQL dataset

In [2]:
path_to_database = r"C:\Users\alito\Desktop\NanceLab\DeepLearning-Model\diff_transformers\project\data"
path_to_code = r"C:\Users\alito\Desktop\NanceLab\DeepLearning-Model\diff_transformers\project"
os.chdir(path_to_database)
track_from_sql =  sql.data_from_sql("database.db", "SELECT * FROM TRACKMATEDATA")
os.chdir(path_to_code)
track_with_frame = df.separate_trajectories(track_from_sql)
trajectories1 = df.separate_data(track_with_frame, False)
trajectories = []
for temp in trajectories1:
    f2 = []
    c = 1
    for t1 in temp:
        f2.append(t1)
        c += 1
        if c == 10:
            break
    trajectories.append(f2)
trajectories

[[(424.4435, 1711.9775),
  (402.177, 1711.2914),
  (424.0598, 1709.0296),
  (430.233, 1703.6202),
  (437.3247, 1694.1591),
  (433.2782, 1687.5521),
  (432.7909, 1690.6145),
  (449.0688, 1695.5747),
  (448.6298, 1692.6731)],
 [(199.5516, 1852.7813),
  (202.5402, 1838.6909),
  (203.0731, 1835.3324),
  (207.5109, 1830.2404),
  (219.6977, 1823.5929),
  (216.0012, 1813.2095),
  (212.2338, 1813.4252),
  (214.5405, 1817.368),
  (214.5307, 1813.6753)],
 [(358.6978, 1727.2507),
  (355.0077, 1734.5474),
  (352.017, 1744.1678),
  (352.8249, 1744.8427),
  (353.6329, 1745.5176),
  (354.4409, 1746.1925),
  (355.2488, 1746.8675),
  (356.0568, 1747.5424),
  (356.8648, 1748.2173)],
 [(341.8735, 1742.8685),
  (332.3119, 1753.2677),
  (330.5376, 1747.3787),
  (331.985, 1749.2015),
  (333.4325, 1751.0244),
  (334.88, 1752.8472),
  (344.7104, 1749.7057),
  (335.2146, 1744.263),
  (356.7546, 1733.8491)],
 [(238.636, 1607.6895),
  (241.3557, 1600.0849),
  (232.1582, 1601.2803),
  (230.3202, 1598.5422),
  (23

Making Fake data

In [20]:
total_size = 10000
max_x = 1000
max_y = 1000
min_x = 0
min_y = 0
track_len = 10

trajectories = dm.create_synthetic(total_size, max_x, max_y, min_x, min_y, track_len)

In [21]:
norm_all_data = df.normalize_data(trajectories)
train, test = df.split_test_train(norm_all_data)
train_data, train_masked_point = df.mask_point_at_index(train, 6)
test_data, test_masked_point = df.mask_point_at_index(test, 6)

print(len(train_data))
print(len(test_masked_point))

9000
1000


In [22]:
src_data_tensor, tgt_data_tensor, src_masks_tensor = df.prepare_data_for_transformer(train_data, train_masked_point)

## DEBUG
print("src_data_tensor shape:", src_data_tensor.shape)
print("tgt_data_tensor shape:", tgt_data_tensor.shape)
print("src_masks_tensor shape:", src_masks_tensor.shape)

[[(0.78642926001969, 0.540867152356828), (0.7889921088994538, 0.540867152356828), (0.7915549577792175, 0.540867152356828), (0.7941178066589812, 0.540867152356828), (0.7966806555387449, 0.540867152356828), (0.7992435044185087, 0.540867152356828), (0.0, 0.0), (0.8043692021780361, 0.540867152356828), (0.8069320510577999, 0.540867152356828), (0.8094948999375635, 0.540867152356828)], [(0.20295399839348333, 0.7826292300145389), (0.20524050552993764, 0.7851686536012585), (0.20752701352067493, 0.7877080780422613), (0.20981352065712922, 0.7902475016289809), (0.2121000286478665, 0.7927869252157007), (0.21438653578432082, 0.7953263496567033), (0.0, 0.0), (0.21895955091151242, 0.8004051968301428), (0.2212460580479667, 0.8029446204168625), (0.22353256603870403, 0.8054840448578652)], [(0.8487919160939406, 0.4699616666833651), (0.8493410389291826, 0.470616085019115), (0.8498901609101414, 0.47127050420914784), (0.8504392837453831, 0.4719249225448978), (0.850988405726342, 0.4725793417349306), (0.851537

In [23]:
import model as md

input_dim = 2
hidden_dim = 128
output_dim = 2
rate = 0.001

model = md.LSTMModel(input_dim, hidden_dim, output_dim)
loss_function = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=rate) ## w 


In [24]:
dataset = TensorDataset(src_data_tensor, tgt_data_tensor, src_masks_tensor)
dataloader = DataLoader(dataset, batch_size=32, shuffle=True)

In [25]:
n_iters = 10

for epoch in range(n_iters):
    total_loss = 0
    for src, tgt, mask in dataloader:
        optimizer.zero_grad()
        output = model(src)
        masked_output = output # output[:, 6, :]
        loss = loss_function(masked_output, tgt)
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
    print(f'Epoch {epoch+1}/{n_iters}, Loss: {total_loss / len(dataloader)}')

Epoch 1/10, Loss: 0.014807300737326537
Epoch 2/10, Loss: 4.038116664515069e-05
Epoch 3/10, Loss: 3.290259222702721e-05
Epoch 4/10, Loss: 3.151557818797197e-05
Epoch 5/10, Loss: 2.202759647611566e-05
Epoch 6/10, Loss: 2.4824429382411152e-05
Epoch 7/10, Loss: 2.077276704728726e-05
Epoch 8/10, Loss: 1.863011698494397e-05
Epoch 9/10, Loss: 1.1367499043238286e-05
Epoch 10/10, Loss: 1.2145898367570296e-05


In [26]:
model.eval()
t_src_data_tensor, t_tgt_data_tensor, t_src_masks_tensor = df.prepare_data_for_transformer(test_data, test_masked_point)
X_test = t_src_data_tensor[3]
with torch.no_grad():
    predictions = model(X_test)
    print(X_test)
    print("Predictions:", predictions)

[[(0.7454236779434705, 0.2982507917391959), (0.7514036586629192, 0.2982507917391959), (0.7573836393823679, 0.2982507917391959), (0.7633636201018166, 0.2982507917391959), (0.7693436008212653, 0.2982507917391959), (0.7753235815407139, 0.2982507917391959), (0.0, 0.0), (0.7872835429796113, 0.2982507917391959), (0.79326352369906, 0.2982507917391959), (0.7992435044185087, 0.2982507917391959)], [(0.6933124173882749, 0.8800174874455601), (0.6899207559950401, 0.8804339307400137), (0.6865290954560881, 0.8808503748887503), (0.6831374340628531, 0.8812668181832037), (0.6797457735239013, 0.8816832614776573), (0.6763541121306663, 0.8820997056263936), (0.0, 0.0), (0.6695707901984795, 0.8829325930695837), (0.6661791288052445, 0.8833490363640372), (0.6627874682662925, 0.8837654796584908)], [(0.8299976909756733, 0.49644443844092356), (0.8351233887352008, 0.49644443844092356), (0.8402490864947282, 0.49644443844092356), (0.8453747842542556, 0.49644443844092356), (0.850500482013783, 0.49644443844092356), (0

In [27]:
def compute_accuracy(predictions, targets, threshold=0.1):
    distances = torch.sqrt(torch.sum((predictions - targets) ** 2, dim=1))
    accurate_predictions = distances < threshold
    accuracy = torch.mean(accurate_predictions.float()) * 100
    return accuracy.item()
predictions = model(t_src_data_tensor)
acc = compute_accuracy(predictions, t_tgt_data_tensor, 0.01)
print('accuracy of model to predict a point: {:.2f} %'.format(acc))

accuracy of model to predict a point: 91.30 %


In [28]:
predictions = model(t_src_data_tensor[0])
print(t_src_data_tensor[0], predictions)

tensor([[0.7454, 0.2983],
        [0.7514, 0.2983],
        [0.7574, 0.2983],
        [0.7634, 0.2983],
        [0.7693, 0.2983],
        [0.7753, 0.2983],
        [0.0000, 0.0000],
        [0.7873, 0.2983],
        [0.7933, 0.2983],
        [0.7992, 0.2983]]) tensor([0.7715, 0.2964], grad_fn=<ViewBackward0>)
